In [1]:
import random
import torch
from imitation.algorithms import preference_comparisons
from imitation.rewards.reward_nets import BasicRewardNet
from imitation.util.networks import RunningNorm
from imitation.util.util import make_vec_env
from imitation.policies.base import FeedForward32Policy, NormalizeFeaturesExtractor
import gymnasium as gym
from stable_baselines3 import PPO
import numpy as np
import pandas as pd
import seals
from imitation.rewards.reward_wrapper import RewardVecEnvWrapper
from stable_baselines3.common.evaluation import evaluate_policy
from tqdm import tqdm
from wandb.integration.sb3 import WandbCallback
import wandb
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.vec_env import DummyVecEnv
from utils.seed import set_seeds
from seals.util import AbsorbAfterDoneWrapper
from gymnasium.wrappers import TimeLimit
from stable_baselines3.common.vec_env import VecFrameStack

/Users/ivanmakarov/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


In [2]:
from imitation_loss.MSELoss import MSELoss
from imitation_loss.PreferenceLoss import PreferenceLoss
from imitation_loss.RatingPreferenceModel import RatingPreferenceModel

In [3]:
def make_env():
    env = gym.make("seals/CartPole-v0")
    #endless_env = AbsorbAfterDoneWrapper(env)
    #limited_env = TimeLimit(endless_env, max_episode_steps=1_000)
    env = Monitor(env)  # record stats such as returns
    return env

In [4]:
rewards = []

def run_experiment(num_comparisons, num_runs=5):
    results = []

    for k in tqdm(range(num_runs)):
        set_seeds(k)
        rng = np.random.default_rng(k)
        venv = DummyVecEnv([make_env])
        run = wandb.init(
            project="rlhf",
            name=f"CartPole_Preference_Improved100_{num_comparisons}_{k}",
            sync_tensorboard=True
        )
        reward_net = BasicRewardNet(
            venv.observation_space, venv.action_space, normalize_input_layer=RunningNorm
        )
        fragmenter = preference_comparisons.RandomFragmenter(
            warning_threshold=0,
            rng=rng
        )
        gatherer = preference_comparisons.SyntheticGatherer(rng=rng, temperature=0)
        preference_model = RatingPreferenceModel(reward_net, list(range(20, 120, 20)), m_mul=100)
        reward_trainer = preference_comparisons.BasicRewardTrainer(
            preference_model=preference_model,
            loss=PreferenceLoss(),
            epochs=10, #10 for Preference, 30 for evaluative
            rng=rng
        )

        agent = PPO(
            policy=FeedForward32Policy,
            policy_kwargs=dict(
                features_extractor_class=NormalizeFeaturesExtractor,
                features_extractor_kwargs=dict(normalize_class=RunningNorm),
            ),
            env=venv,
            seed=k,
            n_steps=2048 // venv.num_envs,
            batch_size=64,
            ent_coef=0.01,
            learning_rate=2e-3,
            clip_range=0.1,
            gae_lambda=0.95,
            gamma=0.97,
            n_epochs=10
        )

        trajectory_generator = preference_comparisons.AgentTrainer(
            algorithm=agent,
            reward_fn=reward_net,
            venv=venv,
            exploration_frac=0.4, # 0.4 for CartPole
            rng=rng,
        )

        pref_comparisons = preference_comparisons.PreferenceComparisons(
            trajectory_generator,
            reward_net,
            num_iterations=60,
            fragmenter=fragmenter,
            preference_gatherer=gatherer,
            reward_trainer=reward_trainer,
            fragment_length=200,
            transition_oversampling=1,
            initial_comparison_frac=0.1,
            allow_variable_horizon=False,
            initial_epoch_multiplier=4,
            query_schedule="hyperbolic"
        )

        if num_comparisons > 0:
            try:
                pref_comparisons.train(
                    total_timesteps=5_000,
                    total_comparisons=num_comparisons,
                )
            except:
                pass

        learned_reward_venv = RewardVecEnvWrapper(venv, reward_net.predict_processed)

        learner = PPO(
            seed=k,
            policy=FeedForward32Policy,
            policy_kwargs=dict(
                features_extractor_class=NormalizeFeaturesExtractor,
                features_extractor_kwargs=dict(normalize_class=RunningNorm),
            ),
            env=learned_reward_venv,
            batch_size=64,
            ent_coef=0.01,
            n_epochs=10,
            n_steps=2048 // learned_reward_venv.num_envs,
            clip_range=0.1,
            gae_lambda=0.95,
            gamma=0.97,
            learning_rate=2e-3,
            tensorboard_log=f"runs/{run.id}"
        )
        learner.learn(500_000, callback=WandbCallback())

        n_eval_episodes = 100
        reward_mean, _ = evaluate_policy(learner.policy, venv, n_eval_episodes)
        results.append(reward_mean)

        run.finish()

        torch.save(reward_net.state_dict(), f'models/reward_net_{num_comparisons}_{k}.pth')

    mean_reward = np.mean(results)
    std_error = np.std(results) / np.sqrt(num_runs)
    return mean_reward, std_error

comparison_counts = [10, 25, 50, 100, 200, 300, 500]
results = {}

for count in comparison_counts:
    mean, std_err = run_experiment(count)
    results[count] = (mean, std_err)


  0%|                                                     | 0/5 [00:00<?, ?it/s]wandb: Currently logged in as: makarov18042003 (ivan-makarov). Use `wandb login --relogin` to force relogin


Query schedule: [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Requested 240 transitions but only 0 in buffer. Sampling 240 additional transitions.
Sampling 160 exploratory transitions.
Creating fragment pairs
Gathering preferences
Dataset now contains 1 comparisons


Training reward model:   0%|          | 0/40 [00:00<?, ?it/s]

Training agent for 83 timesteps
---------------------------------------------------
| raw/                                 |          |
|    agent/rollout/ep_len_mean         | 500      |
|    agent/rollout/ep_rew_mean         | 26.5     |
|    agent/rollout/ep_rew_wrapped_mean | 90.3     |
|    agent/time/fps                    | 4404     |
|    agent/time/iterations             | 1        |
|    agent/time/time_elapsed           | 0        |
|    agent/time/total_timesteps        | 2048     |
---------------------------------------------------
---------------------------------------------------
| mean/                                |          |
|    agent/rollout/ep_len_mean         | 500      |
|    agent/rollout/ep_rew_mean         | 26.5     |
|    agent/rollout/ep_rew_wrapped_mean | 90.3     |
|    agent/time/fps                    | 4.4e+03  |
|    agent/time/iterations             | 1        |
|    agent/time/time_elapsed           | 0        |
|    agent/time/total_timesteps 

Training reward model:   0%|          | 0/10 [00:00<?, ?it/s]

...

Training agent for 103 timesteps
------------------------------------------------------
| raw/                                 |             |
|    agent/rollout/ep_len_mean         | 500         |
|    agent/rollout/ep_rew_mean         | 395         |
|    agent/rollout/ep_rew_wrapped_mean | 303         |
|    agent/time/fps                    | 3659        |
|    agent/time/iterations             | 1           |
|    agent/time/time_elapsed           | 0           |
|    agent/time/total_timesteps        | 122880      |
|    agent/train/approx_kl             | 0.004482505 |
|    agent/train/clip_fraction         | 0.141       |
|    agent/train/clip_range            | 0.1         |
|    agent/train/entropy_loss          | -0.422      |
|    agent/train/explained_variance    | 0.933       |
|    agent/train/learning_rate         | 0.002       |
|    agent/train/loss                  | 0.00781     |
|    agent/train/n_updates             | 590         |
|    agent/train/policy_gradient

Training reward model:   0%|          | 0/10 [00:00<?, ?it/s]

Training agent for 83 timesteps
-------------------------------------------------------
| raw/                                 |              |
|    agent/rollout/ep_len_mean         | 500          |
|    agent/rollout/ep_rew_mean         | 409          |
|    agent/rollout/ep_rew_wrapped_mean | 319          |
|    agent/time/fps                    | 3736         |
|    agent/time/iterations             | 1            |
|    agent/time/time_elapsed           | 0            |
|    agent/time/total_timesteps        | 124928       |
|    agent/train/approx_kl             | 0.0025538523 |
|    agent/train/clip_fraction         | 0.143        |
|    agent/train/clip_range            | 0.1          |
|    agent/train/entropy_loss          | -0.42        |
|    agent/train/explained_variance    | 0.966        |
|    agent/train/learning_rate         | 0.002        |
|    agent/train/loss                  | 0.0336       |
|    agent/train/n_updates             | 600          |
|    agent/train

wandb: WARNING When using several event log directories, please call `wandb.tensorboard.patch(root_logdir="...")` before `wandb.init`


100%|████████████████████████████████████████████| 5/5 [31:46<00:00, 381.23s/it]


In [5]:
import pandas as pd
results_df = pd.DataFrame(results, index=["Mean Reward", "Standard Error"]).T

# Save the DataFrame to a CSV file
results_df.to_csv("cartpole_preference_improved100.csv")


In [6]:
results_df

Mean Reward  Standard Error
10       106.144       85.203645
25        13.024        2.674473
50       201.362       97.819847
100      210.562      105.654535
200      160.810       79.040042
300      432.054       60.772750
500      450.048       44.678427

In [ ]:
import matplotlib.pyplot as plt

# Ensure the index is integers for plotting
results_df.index = results_df.index.astype(int)

# Plot the data with error bars and connecting lines
plt.figure(figsize=(10, 6))
plt.errorbar(results_df.index, results_df['Mean Reward'], yerr=results_df['Standard Error'], fmt='-o', ecolor='r', capsize=5, label='Mean Reward')

plt.xlabel('Number of Comparisons')
plt.ylabel('Mean Reward')
plt.title('Mean Reward with Standard Error for Different Numbers of Comparisons')
plt.legend()
plt.grid(True)
plt.show()
